In [20]:
import shutil
import tensorflow as tf
from tensorflow.keras import backend as K
from tensorflow.keras.layers import Activation, Lambda, GlobalAveragePooling2D, concatenate
from tensorflow.keras.layers import UpSampling2D, Conv2D, Dropout, MaxPooling2D, Conv2DTranspose
from tensorflow.keras.layers import Dense, Flatten, Input
from tensorflow.keras.models import Model, Sequential, load_model
from tensorflow.keras.callbacks import ModelCheckpoint, ReduceLROnPlateau
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import cv2
import pickle
import random
import os

In [35]:
from src.metrics import IOU


In [36]:
IMG_HEIGHT = 512
IMG_WIDTH = 512
img_dir = '/images'

In [38]:
EPOCHS = 30
batch_size = 16

### Unet model

In [39]:
class Unet():
    def __init__(self, num_classes=1):
        self.num_classes=num_classes

    def build_model(self):
        in1 = Input(shape=(IMG_HEIGHT, IMG_WIDTH, 3 ))

        conv1 = Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(in1)
        conv1 = Dropout(0.2)(conv1)
        conv1 = Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv1)
        pool1 = MaxPooling2D((2, 2))(conv1)

        conv2 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(pool1)
        conv2 = Dropout(0.2)(conv2)
        conv2 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv2)
        pool2 = MaxPooling2D((2, 2))(conv2)

        conv3 = Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(pool2)
        conv3 = Dropout(0.2)(conv3)
        conv3 = Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv3)
        pool3 = MaxPooling2D((2, 2))(conv3)

        conv4 = Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(pool3)
        conv4 = Dropout(0.2)(conv4)
        conv4 = Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv4)

        up1 = concatenate([UpSampling2D((2, 2))(conv4), conv3], axis=-1)
        conv5 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(up1)
        conv5 = Dropout(0.2)(conv5)
        conv5 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv5)
        
        up2 = concatenate([UpSampling2D((2, 2))(conv5), conv2], axis=-1)
        conv6 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(up2)
        conv6 = Dropout(0.2)(conv6)
        conv6 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv6)

        up2 = concatenate([UpSampling2D((2, 2))(conv6), conv1], axis=-1)
        conv7 = Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(up2)
        conv7 = Dropout(0.2)(conv7)
        conv7 = Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv7)
        segmentation = Conv2D(self.num_classes, (1, 1), activation='sigmoid', name='seg')(conv7)
        #segmentation = Conv2D(3, (1, 1), activation='sigmoid', name='seg')(conv7)
        model = Model(inputs=[in1], outputs=[segmentation])

        return model

    

In [43]:
from src.loss import jaccard_loss

In [40]:
model = Unet(num_classes=1).build_model()

compile_params ={
    'loss':jaccard_loss(smooth=90), 
    'optimizer':'rmsprop',
    'metrics':[IOU]
    }
    
                
model.compile(**compile_params)

tf.keras.utils.plot_model(model, show_shapes=True)

model_name = "models/unet.h5"

modelcheckpoint = ModelCheckpoint(model_name,
                                  monitor='val_loss',
                                  mode='auto',
                                  verbose=1,
                                  save_best_only=True)


history = model.fit_generator(train_gen,
                    validation_data=val_gen,
                    epochs=EPOCHS,
                    steps_per_epoch=100,
                    validation_steps = 100,
                    shuffle=True,
                    validation_freq=1
)

NameError: name 'jaccard_loss' is not defined